# Caffe 输入层

In [1]:
from pathlib import Path
from tvm_book.config import env
# 设置 caffeprotobuf环境
env.set_caffeproto(Path(env.__file__).parents[3]/"tests/caffeproto")
# 设置tvm环境
env.set_tvm("/media/pc/data/board/arria10/lxw/tasks/tvm-test")

In [2]:
from pathlib import Path
from google.protobuf import text_format
import caffe_pb2 as pb2

temp_dir = Path(".temp")
temp_dir.mkdir(exist_ok=True)

In [3]:
def parse_input(predict_net):
    old_caffe = False
    if len(predict_net.input) != 0:  # old caffe version
        old_caffe = True
        model_inputs = list(predict_net.input)
        if len(predict_net.input_shape) !=0:
            shapes = [list(sp.dim) for sp in predict_net.input_shape]
        else:
            assert len(model_inputs) == 1
            shapes = [list(predict_net.input_dim)]
    else:
        model_inputs = []
        shapes = []
        for pl in predict_net.layer:
            if pl.type == "Input":
                assert len(pl.top) == 1, "The number of Input layer's output is more than 1."
                model_inputs.append(pl.top[0])
                shapes.append(list(pl.input_param.shape[0].dim))
    return model_inputs, shapes

输入层有两种写法：

## 新的写法

### 单数入

In [4]:
text = """
layer {
  name: "data"
  type: "Input"
  top: "data"
  input_param {
    shape: { dim: 1 dim: 1 dim: 120 dim: 120 }
  }
}
""".strip()
predict_net = pb2.NetParameter()
pl = text_format.Merge(text, predict_net)
pl

layer {
  name: "data"
  type: "Input"
  top: "data"
  input_param {
    shape {
      dim: 1
      dim: 1
      dim: 120
      dim: 120
    }
  }
}

In [5]:
parse_input(predict_net)

(['data'], [[1, 1, 120, 120]])

### 多输入

In [6]:
text = """
layer {
  name: "data1"
  type: "Input"
  top: "data1"
  input_param {
    shape: { dim: 1 dim: 3 dim: 120 dim: 120 }
  }
}

layer {
  name: "data2"
  type: "Input"
  top: "data2"
  input_param {
    shape: { dim: 1 dim: 1 dim: 32 dim: 32 }
  }
}
""".strip()
predict_net = pb2.NetParameter()
pl = text_format.Merge(text, predict_net)
pl

layer {
  name: "data1"
  type: "Input"
  top: "data1"
  input_param {
    shape {
      dim: 1
      dim: 3
      dim: 120
      dim: 120
    }
  }
}
layer {
  name: "data2"
  type: "Input"
  top: "data2"
  input_param {
    shape {
      dim: 1
      dim: 1
      dim: 32
      dim: 32
    }
  }
}

In [7]:
pl.input

[]

In [8]:
parse_input(predict_net)

(['data1', 'data2'], [[1, 3, 120, 120], [1, 1, 32, 32]])

## 旧的写法

## 多输入

In [9]:
input_layer = """
name: "MultiInput"
# 定义所有输入名称
input: ["data1", "data2"]

# 第一个输入的维度配置
input_shape {
  dim: 1    # 批次大小
  dim: 3    # 通道数
  dim: 224  # 高度
  dim: 224  # 宽度
}

# 第二个输入的维度配置
input_shape {
  dim: 1    # 批次大小
  dim: 1    # 通道数
  dim: 112  # 高度
  dim: 112  # 宽度
}
""".strip()
predict_net = pb2.NetParameter()
pl = text_format.Merge(input_layer, predict_net)
pl

name: "MultiInput"
input: "data1"
input: "data2"
input_shape {
  dim: 1
  dim: 3
  dim: 224
  dim: 224
}
input_shape {
  dim: 1
  dim: 1
  dim: 112
  dim: 112
}

In [10]:
parse_input(predict_net)

(['data1', 'data2'], [[1, 3, 224, 224], [1, 1, 112, 112]])

## 单输入

有两种写法：

In [11]:
input_layer = """
name: "单输入"
# 定义所有输入名称
input: "data"

# 输入的维度配置
input_shape {
  dim: 1    # 批次大小
  dim: 3    # 通道数
  dim: 224  # 高度
  dim: 224  # 宽度
}

""".strip()
predict_net = pb2.NetParameter()
pl = text_format.Merge(input_layer, predict_net)
pl

name: "单输入"
input: "data"
input_shape {
  dim: 1
  dim: 3
  dim: 224
  dim: 224
}

In [12]:
parse_input(predict_net)

(['data'], [[1, 3, 224, 224]])

In [13]:
input_layer = """
name: "单输入"
# 定义所有输入名称
input: "data"

# 输入的维度配置
input_dim: 1
input_dim: 3
input_dim: 32
input_dim: 32
""".strip()
predict_net = pb2.NetParameter()
pl = text_format.Merge(input_layer, predict_net)
pl

name: "单输入"
input: "data"
input_dim: 1
input_dim: 3
input_dim: 32
input_dim: 32

In [14]:
parse_input(predict_net)

(['data'], [[1, 3, 32, 32]])